# Shifting home from Brooklyn to Queens Dilemma.

## Introduction & Problem Statement

In this Report let us Examine the neighborhoods of  Brooklyn and Queens. Assuming Person X is moving from Brooklyn heights to Queens and wants to find out suitable neighborhoods similar to Brooklyn Heights in Queens.

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np 

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from geopy.geocoders import Nominatim 
import requests 
from pandas.io.json import json_normalize 


import matplotlib.cm as cm
import matplotlib.colors as colors


from sklearn.cluster import KMeans

import folium

<a id='item1'></a>

## 1. Download and Explore Dataset

### Description of the data and how it will be used to solve the problem

#### Step 1: 

The New York Dataset has a total of 5 boroughs and 306 neighborhoods.
The dataset is Available in :  https://geo.nyu.edu/catalog/nyu_2451_34572

#### Step 2:
Find the venues in each Neighborhood and compare the same with Brooklyn Heights. 

#### Step 3:
Cluster the neighborhoods based on its venues

#### Step 4:
Find the cluster that has maximum number of Neighborhoods similar to Brooklyn Heights and Suggest them as possible neighborhoods which person X can shift to


For your convenience, I downloaded the files and placed it on the server, so you can simply run a `wget` command and access the data. So let's go ahead and do that.

In [2]:
#!w -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
#print('Data downloaded!')

import wget
url = 'https://cocl.us/new_york_dataset/nyu_2451_34572-geo.json'
filename = wget.download(url)

In [3]:
filename

'nyu_2451_34572-geo.json'

#### Load and explore the data

Next, let's load the data.

In [4]:
import json
with open('nyu_2451_34572-geo.json') as json_data:
    newyork_data = json.load(json_data);

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

Let's take a quick look at the data.

Notice how all the relevant data is in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [6]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.

In [7]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [8]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [9]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

let's loop through the data and fill the dataframe one row at a time.

In [10]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
neighborhoods.Borough.unique()

array(['Bronx', 'Manhattan', 'Brooklyn', 'Queens', 'Staten Island'],
      dtype=object)

In [13]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


Let Us Check the number of Neighborhoods in each borough

In [14]:
neighborhoods.groupby(['Borough']).size()

Borough
Bronx            52
Brooklyn         70
Manhattan        40
Queens           81
Staten Island    63
dtype: int64

#### We Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [15]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [16]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

However, for illustration purposes, let's simplify the above map and segment and cluster only the neighborhoods in Brooklyn. So let's slice the original dataframe and create a new dataframe of the Brooklyn data.

In [17]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data

Borough               Neighborhood   Latitude  Longitude
0   Brooklyn                  Bay Ridge  40.625801 -74.030621
1   Brooklyn                Bensonhurst  40.611009 -73.995180
2   Brooklyn                Sunset Park  40.645103 -74.010316
3   Brooklyn                 Greenpoint  40.730201 -73.954241
4   Brooklyn                  Gravesend  40.595260 -73.973471
5   Brooklyn             Brighton Beach  40.576825 -73.965094
6   Brooklyn             Sheepshead Bay  40.586890 -73.943186
7   Brooklyn          Manhattan Terrace  40.614433 -73.957438
8   Brooklyn                   Flatbush  40.636326 -73.958401
9   Brooklyn              Crown Heights  40.670829 -73.943291
10  Brooklyn              East Flatbush  40.641718 -73.936103
11  Brooklyn                 Kensington  40.642382 -73.980421
12  Brooklyn            Windsor Terrace  40.656946 -73.980073
13  Brooklyn           Prospect Heights  40.676822 -73.964859
14  Brooklyn                Brownsville  40.663950 -73.910235
15  Brooklyn               Williamsburg  40.707144 -73.958115
16  Brooklyn                   Bushwick  40.698116 -73.925258
17  Brooklyn         Bedford Stuyvesant  40.687232 -73.941785
18  Brooklyn           Brooklyn Heights  40.695864 -73.993782
19  Brooklyn                Cobble Hill  40.687920 -73.998561
20  Brooklyn            Carroll Gardens  40.680540 -73.994654
21  Brooklyn                   Red Hook  40.676253 -74.012759
22  Brooklyn                    Gowanus  40.673931 -73.994441
23  Brooklyn                Fort Greene  40.688527 -73.972906
24  Brooklyn                 Park Slope  40.672321 -73.977050
25  Brooklyn              Cypress Hills  40.682391 -73.876616
26  Brooklyn              East New York  40.669926 -73.880699
27  Brooklyn              Starrett City  40.647589 -73.879370
28  Brooklyn                   Canarsie  40.635564 -73.902093
29  Brooklyn                  Flatlands  40.630446 -73.929113
30  Brooklyn                Mill Island  40.606336 -73.908186
31  Brooklyn            Manhattan Beach  40.577914 -73.943537
32  Brooklyn               Coney Island  40.574293 -73.988683
33  Brooklyn                 Bath Beach  40.599519 -73.998752
34  Brooklyn               Borough Park  40.633131 -73.990498
35  Brooklyn              Dyker Heights  40.619219 -74.019314
36  Brooklyn            Gerritsen Beach  40.590848 -73.930102
37  Brooklyn                Marine Park  40.609748 -73.931344
38  Brooklyn               Clinton Hill  40.693229 -73.967843
39  Brooklyn                   Sea Gate  40.576375 -74.007873
40  Brooklyn                   Downtown  40.690844 -73.983463
41  Brooklyn                Boerum Hill  40.685683 -73.983748
42  Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899
43  Brooklyn                 Ocean Hill  40.678403 -73.913068
44  Brooklyn                  City Line  40.678570 -73.867976
45  Brooklyn               Bergen Beach  40.615150 -73.898556
46  Brooklyn                    Midwood  40.625596 -73.957595
47  Brooklyn        Prospect Park South  40.647009 -73.962613
48  Brooklyn                 Georgetown  40.623845 -73.916075
49  Brooklyn          East Williamsburg  40.708492 -73.938858
50  Brooklyn                 North Side  40.714823 -73.958809
51  Brooklyn                 South Side  40.710861 -73.958001
52  Brooklyn              Ocean Parkway  40.613060 -73.968367
53  Brooklyn              Fort Hamilton  40.614768 -74.031979
54  Brooklyn                Ditmas Park  40.643675 -73.961013
55  Brooklyn                    Wingate  40.660947 -73.937187
56  Brooklyn                      Rugby  40.655572 -73.926882
57  Brooklyn             Remsen Village  40.652117 -73.916653
58  Brooklyn                   New Lots  40.662744 -73.885118
59  Brooklyn            Paerdegat Basin  40.631318 -73.902335
60  Brooklyn                 Mill Basin  40.615974 -73.915154
61  Brooklyn               Fulton Ferry  40.703281 -73.995508
62  Brooklyn               Vinegar Hill  40.703321 -73.981116
63  Brooklyn                 Weeksvil

Let us bring the Current Residing Place into one Dataframe

In [18]:
brooklyn_my_place = brooklyn_data[brooklyn_data['Neighborhood']=='Brooklyn Heights'].reset_index(drop=True)

In [19]:
brooklyn_my_place.shape

(1, 4)

In [20]:
# First Let us get the Co Ordinates of Brooklyn
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Brooklyn are 40.6501038, -73.9495823.


In [21]:
# create map of Brooklyn using latitude and longitude values
map_brooklyn = folium.Map(location=[latitude, longitude], zoom_start=11)

# Add Initial Markups
for lat, lng, label in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude'], brooklyn_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)
    
# Add the Current Residing Place
for lat, lng, name in zip(brooklyn_my_place['Latitude'], brooklyn_my_place['Longitude'], brooklyn_my_place['Neighborhood']):
    folium.Marker(
        [lat, lng],
        icon= folium.Icon(color='red'), 
        popup=name).add_to(map_brooklyn)
    
map_brooklyn

In [22]:
# Similar to the above get the details of Queens 

queens_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
queens_data

Borough          Neighborhood   Latitude  Longitude
0   Queens               Astoria  40.768509 -73.915654
1   Queens              Woodside  40.746349 -73.901842
2   Queens       Jackson Heights  40.751981 -73.882821
3   Queens              Elmhurst  40.744049 -73.881656
4   Queens          Howard Beach  40.654225 -73.838138
5   Queens                Corona  40.742382 -73.856825
6   Queens          Forest Hills  40.725264 -73.844475
7   Queens           Kew Gardens  40.705179 -73.829819
8   Queens         Richmond Hill  40.697947 -73.831833
9   Queens              Flushing  40.764454 -73.831773
10  Queens      Long Island City  40.750217 -73.939202
11  Queens             Sunnyside  40.740176 -73.926916
12  Queens         East Elmhurst  40.764073 -73.867041
13  Queens               Maspeth  40.725427 -73.896217
14  Queens             Ridgewood  40.708323 -73.901435
15  Queens              Glendale  40.702762 -73.870742
16  Queens             Rego Park  40.728974 -73.857827
17  Queens             Woodhaven  40.689887 -73.858110
18  Queens            Ozone Park  40.680708 -73.843203
19  Queens      South Ozone Park  40.668550 -73.809865
20  Queens         College Point  40.784903 -73.843045
21  Queens            Whitestone  40.781291 -73.814202
22  Queens               Bayside  40.766041 -73.774274
23  Queens            Auburndale  40.761730 -73.791762
24  Queens           Little Neck  40.770826 -73.738898
25  Queens            Douglaston  40.766846 -73.742498
26  Queens             Glen Oaks  40.749441 -73.715481
27  Queens             Bellerose  40.728573 -73.720128
28  Queens     Kew Gardens Hills  40.722578 -73.820878
29  Queens         Fresh Meadows  40.734394 -73.782713
30  Queens             Briarwood  40.710935 -73.811748
31  Queens        Jamaica Center  40.704657 -73.796902
32  Queens       Oakland Gardens  40.745619 -73.754950
33  Queens        Queens Village  40.718893 -73.738715
34  Queens                Hollis  40.711243 -73.759250
35  Queens         South Jamaica  40.696911 -73.790426
36  Queens            St. Albans  40.694445 -73.758676
37  Queens              Rochdale  40.675211 -73.772588
38  Queens   Springfield Gardens  40.666230 -73.760421
39  Queens       Cambria Heights  40.692775 -73.735269
40  Queens              Rosedale  40.659816 -73.735261
41  Queens          Far Rockaway  40.603134 -73.754980
42  Queens         Broad Channel  40.603027 -73.820055
43  Queens          Breezy Point  40.557401 -73.925512
44  Queens              Steinway  40.775923 -73.902290
45  Queens            Beechhurst  40.792781 -73.804365
46  Queens           Bay Terrace  40.782843 -73.776802
47  Queens              Edgemere  40.595642 -73.776133
48  Queens               Arverne  40.589144 -73.791992
49  Queens        Rockaway Beach  40.582802 -73.822361
50  Queens              Neponsit  40.572037 -73.857547
51  Queens           Murray Hill  40.764126 -73.812763
52  Queens           Floral Park  40.741378 -73.708847
53  Queens            Holliswood  40.720957 -73.767142
54  Queens       Jamaica Estates  40.716805 -73.787227
55  Queens       Queensboro Hill  40.744572 -73.825809
56  Queens             Hillcrest  40.723825 -73.797603
57  Queens            Ravenswood  40.761705 -73.931575
58  Queens            Lindenwood  40.663918 -73.849638
59  Queens             Laurelton  40.667884 -73.740256
60  Queens           Lefrak City  40.736075 -73.862525
61  Queens          Belle Harbor  40.576156 -73.854018
62  Queens         Rockaway Park  40.580343 -73.841534
63  Queens            Somerville  40.597711 -73.796648
64  Queens            Brookville  40.660003 -73.751753
65  Queens              Bellaire  40.733014 -73.738892
66  Queens          North Corona  40.754071 -73.857518
67  Queens  Forest Hills Gardens  40.714611 -73.841022
68  Queens         Jamaica Hills  40.711460 -73.796465
69  Queens                Utopia  40.733500 -73.796717
70  Queens               Pomonok  40.734936 -73.804861
71  Queens       Astoria Heights  40.770317

In [23]:
# Getting the Co Ordinates of Queens

address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Brooklyn are 40.7498243, -73.7976337.


In [24]:
# Locating the Neighborhoods of Queens in a Map
map_queens = folium.Map(location=[latitude, longitude], zoom_start=11)

# add queens markers to map
for lat, lng, label in zip(queens_data['Latitude'], queens_data['Longitude'], queens_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#FF0000',
        fill_opacity=0.7,
        parse_html=False).add_to(map_queens)
    
map_queens

In [25]:
# create map of New York using latitude and longitude values and placing the From and To Place
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add brooklyn markers to map
for lat, lng, label in zip(brooklyn_data['Latitude'], brooklyn_data['Longitude'], brooklyn_data['Neighborhood']):
    label = folium.Popup(label)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)
    
# add the initial place markers to map
for lat, lng, name in zip(brooklyn_my_place['Latitude'], brooklyn_my_place['Longitude'], brooklyn_my_place['Neighborhood']):
    folium.Marker(
        [lat, lng],
        icon= folium.Icon(color='red'), 
        popup=name).add_to(map_newyork)
    
# add queens markers to map
for lat, lng, label in zip(queens_data['Latitude'], queens_data['Longitude'], queens_data['Neighborhood']):
    label = folium.Popup(label)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#FF0000',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)
    

map_newyork

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

#### Let's explore person X's neighborhood in our dataframe.

Get the current neighborhood's name.

In [27]:
brooklyn_my_place.loc[0,'Neighborhood']

'Brooklyn Heights'

Get the current neighborhood's latitude and longitude values.

In [28]:
neighborhood_latitude = brooklyn_my_place.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = brooklyn_my_place.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = brooklyn_my_place.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Brooklyn Heights are 40.695863722724084, -73.99378225496424.


First, let's create the GET request URL. Name your URL **url**.

In [29]:
# type your answer here
LIMIT =100
radius =500

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=JCTZHODKAHSDGONDJGOWVSUN1S1LXKLQRNH33K0MOARNJS5R&client_secret=QE5SLCGXCRZKPPEE4FX2I5XSSONDCT4X5HW4TMYLYOHJYFO1&v=20180605&ll=40.695863722724084,-73.99378225496424&radius=500&limit=100'

Double-click __here__ for the solution.
<!-- The correct answer is:
LIMIT = 100 # limit of number of venues returned by Foursquare API
-->

<!--
radius = 500 # define radius
-->

<!--
\\ # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL
--> 

Send the GET request and examine the resutls

In [30]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e8f44c41e152c001b6fbc1d'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Brooklyn Heights',
  'headerFullLocation': 'Brooklyn Heights, Brooklyn',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 112,
  'suggestedBounds': {'ne': {'lat': 40.70036372722409,
    'lng': -73.9878580758486},
   'sw': {'lat': 40.69136371822408, 'lng': -73.99970643407988}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4a919ad7f964a520e81a20e3',
       'name': 'Brooklyn Historical Society',
       'location': {'address': '128 Pierrepont St',
        'crossStreet': 'at Clinton St',
        'lat': 40.694941993032

In [31]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [32]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name        categories        lat        lng
0  Brooklyn Historical Society    History Museum  40.694942 -73.992333
1                 Dellarocco's       Pizza Place  40.694992 -73.995924
2                Sushi Gallery  Sushi Restaurant  40.697595 -73.993236
3              Emack & Bolio's    Ice Cream Shop  40.694987 -73.994946
4              Area Yoga & Spa       Yoga Studio  40.694568 -73.993514

In [33]:
# Number of Venues returned by foursquare 
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in Queens

#### Let's create a function to repeat the same process to all the neighborhoods in Queens

In [34]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *queen_venues*.

In [35]:
# type your answer here

queens_venues = getNearbyVenues(names=queens_data['Neighborhood'],
                                   latitudes=queens_data['Latitude'],
                                   longitudes=queens_data['Longitude']
                                  )


Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


#### Let's check the size of the resulting dataframe

In [36]:
print(queens_venues.shape)
queens_venues.head()

(2089, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0        Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1      Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2    Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3     CrossFit Queens       40.769404       -73.918977                   Gym  
4  Simply Fit Astoria       40.769114       -73.912403                   Gym

In [37]:
type(queens_venues)

pandas.core.frame.DataFrame

In [38]:
queens_venues['Borough']='Queens'

Let's check how many venues were returned for each neighborhood

In [39]:
queens_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                 100                     100    100   
Astoria Heights                          13                      13     13   
Auburndale                               20                      20     20   
Bay Terrace                              37                      37     37   
Bayside                                  69                      69     69   
Bayswater                                 2                       2      2   
Beechhurst                               12                      12     12   
Bellaire                                 14                      14     14   
Belle Harbor                             17                      17     17   
Bellerose                                22                      22     22   
Blissville                               18                      18     18   
Breezy Point                              4                       4      4   
Briarwood                                11                      11     11   
Broad Channel                             5                       5      5   
Brookville                                1                       1      1   
Cambria Heights                          14                      14     14   
College Point                            39                      39     39   
Corona                                   16                      16     16   
Douglaston                               18                      18     18   
East Elmhurst                            12                      12     12   
Edgemere                                 14                      14     14   
Elmhurst                                 30                      30     30   
Far Rockaway                             31                      31     31   
Floral Park                               7                       7      7   
Flushing                                 53                      53     53   
Forest Hills                             38                      38     38   
Forest Hills Gardens                     23                      23     23   
Fresh Meadows                            14                      14     14   
Glen Oaks                                21                      21     21   
Glendale                                  4                       4      4   
Hammels                                  19                      19     19   
Hillcrest                                20                      20     20   
Hollis                                   14                      14     14   
Holliswood                                5                       5      5   
Howard Beach                             36                      36     36   
Hunters Point                            67                      67     67   
Jackson Heights                          83                      83     83   
Jamaica Center                           43                      43     43   
Jamaica Estates                           4                       4      4   
Jamaica Hills                            29                      29     29   
Kew Gardens                              46                      46     46   
Kew Gardens Hills                        24                      24     24   
Laurelton                                 5                       5      5   
Lefrak City                              23                      23     23   
Lindenwood                               12                      12     12   
Little Neck                              48                      48     48   
Long Island City                         71                      71     71   
Malba                                     3                       3      3   
Maspeth                                  34 

#### Let's find out how many unique categories can be curated from all the returned venues

In [40]:
print('There are {} uniques categories.'.format(len(queens_venues['Venue Category'].unique())))

There are 265 uniques categories.


In [41]:
queens_venues.columns

Index(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude',
       'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category',
       'Borough'],
      dtype='object')

In [42]:
# Getting the Brooklyn Venues

brooklyn_venues = getNearbyVenues(names=brooklyn_my_place['Neighborhood'],
                                   latitudes=brooklyn_my_place['Latitude'],
                                   longitudes=brooklyn_my_place['Longitude']
                                  )



Brooklyn Heights


In [43]:
brooklyn_venues['Borough']='Brooklyn'

In [44]:
print(brooklyn_venues.shape)
brooklyn_venues.head()

(100, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Brooklyn Heights              40.695864              -73.993782   
1  Brooklyn Heights              40.695864              -73.993782   
2  Brooklyn Heights              40.695864              -73.993782   
3  Brooklyn Heights              40.695864              -73.993782   
4  Brooklyn Heights              40.695864              -73.993782   

                         Venue  Venue Latitude  Venue Longitude  \
0  Brooklyn Historical Society       40.694942       -73.992333   
1                 Dellarocco's       40.694992       -73.995924   
2                Sushi Gallery       40.697595       -73.993236   
3              Emack & Bolio's       40.694987       -73.994946   
4              Area Yoga & Spa       40.694568       -73.993514   

     Venue Category   Borough  
0    History Museum  Brooklyn  
1       Pizza Place  Brooklyn  
2  Sushi Restaurant  Brooklyn  
3    Ice Cream Shop  Brooklyn  
4       Yoga Studio  Brooklyn

In [45]:
type(brooklyn_venues)

pandas.core.frame.DataFrame

In [46]:
brooklyn_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                             
Brooklyn Heights                    100                     100    100   

                  Venue Latitude  Venue Longitude  Venue Category  Borough  
Neighborhood                                                                
Brooklyn Heights             100              100             100      100

In [47]:
# Merging the Data To Compare Queens and Brooklyn Venues

merged_neighborhoods=pd.concat([queens_venues, brooklyn_venues], ignore_index=True)

In [48]:
merged_neighborhoods.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                 100                     100    100   
Astoria Heights                          13                      13     13   
Auburndale                               20                      20     20   
Bay Terrace                              37                      37     37   
Bayside                                  69                      69     69   
Bayswater                                 2                       2      2   
Beechhurst                               12                      12     12   
Bellaire                                 14                      14     14   
Belle Harbor                             17                      17     17   
Bellerose                                22                      22     22   
Blissville                               18                      18     18   
Breezy Point                              4                       4      4   
Briarwood                                11                      11     11   
Broad Channel                             5                       5      5   
Brooklyn Heights                        100                     100    100   
Brookville                                1                       1      1   
Cambria Heights                          14                      14     14   
College Point                            39                      39     39   
Corona                                   16                      16     16   
Douglaston                               18                      18     18   
East Elmhurst                            12                      12     12   
Edgemere                                 14                      14     14   
Elmhurst                                 30                      30     30   
Far Rockaway                             31                      31     31   
Floral Park                               7                       7      7   
Flushing                                 53                      53     53   
Forest Hills                             38                      38     38   
Forest Hills Gardens                     23                      23     23   
Fresh Meadows                            14                      14     14   
Glen Oaks                                21                      21     21   
Glendale                                  4                       4      4   
Hammels                                  19                      19     19   
Hillcrest                                20                      20     20   
Hollis                                   14                      14     14   
Holliswood                                5                       5      5   
Howard Beach                             36                      36     36   
Hunters Point                            67                      67     67   
Jackson Heights                          83                      83     83   
Jamaica Center                           43                      43     43   
Jamaica Estates                           4                       4      4   
Jamaica Hills                            29                      29     29   
Kew Gardens                              46                      46     46   
Kew Gardens Hills                        24                      24     24   
Laurelton                                 5                       5      5   
Lefrak City                              23                      23     23   
Lindenwood                               12                      12     12   
Little Neck                              48                      48     48   
Long Island City                         71                      71     71   
Malba                                     3 

<a id='item3'></a>

## 3. Compare The Neighborhoods of Queens and Brooklyn Heights

In [49]:
# one hot encoding
queens_venues_onehot = pd.get_dummies(merged_neighborhoods[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
# queens_venues_onehot['Borough'] = merged_neighborhoods['Borough']
queens_venues_onehot['Neighborhood'] = merged_neighborhoods['Neighborhood'] 
# move neighborhood column to the first column
fixed_columns = [queens_venues_onehot.columns[-1]] + list(queens_venues_onehot.columns[:-1])
queens_venues_onehot = queens_venues_onehot[fixed_columns]

queens_venues_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
0            0                  0                  0                 0   
1            0                  0                  0                 0   
2            0                  0                  0                 0   
3            0                  0                  0                 0   
4            0                  0                  0                 0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                 0           0      0          0                0   
1                 0           0      0          0                0   
2                 0           0      0          0                0   
3                 0           0      0          0                0   
4                 0           0      0          0                0   

   Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  Boutique  \
0            0           0       0           0          0         0   
1            0           0       0           0          0         0   
2            0           0       0           0          0         0   
3            0           0       0           0          0         0   
4            0           0       0           0          0         0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0                     1               0        0   
1              0                     0               0        0   
2              0                     0               0        0   
3              0                     0               0        0   
4              0                     0               0        0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  \
0            0         0                 0        0     0   
1            0         0              

And let's examine the new dataframe size.

In [50]:
queens_venues_onehot.shape

(2189, 269)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [51]:
queens_grouped = queens_venues_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.027027           0.000000   
5                Bayside     0.014493           0.000000           0.000000   
6              Bayswater     0.000000           0.000000           0.000000   
7             Beechhurst     0.083333           0.000000           0.000000   
8               Bellaire     0.000000           0.000000           0.000000   
9           Belle Harbor     0.000000           0.000000           0.000000   
10             Bellerose     0.000000           0.000000           0.000000   
11            Blissville     0.000000           0.000000           0.000000   
12          Breezy Point     0.000000           0.000000           0.000000   
13             Briarwood     0.000000           0.000000           0.000000   
14         Broad Channel     0.000000           0.000000           0.000000   
15      Brooklyn Heights     0.040000           0.000000           0.000000   
16            Brookville     0.000000           0.000000           0.000000   
17       Cambria Heights     0.000000           0.000000           0.000000   
18         College Point     0.000000           0.000000           0.000000   
19                Corona     0.000000           0.000000           0.000000   
20            Douglaston     0.000000           0.000000           0.000000   
21         East Elmhurst     0.000000           0.000000           0.000000   
22              Edgemere     0.000000           0.000000           0.000000   
23              Elmhurst     0.000000           0.000000           0.000000   
24          Far Rockaway     0.000000           0.000000           0.000000   
25           Floral Park     0.000000           0.000000           0.000000   
26              Flushing     0.018868           0.000000           0.000000   
27          Forest Hills     0.052632           0.000000           0.000000   
28  Forest Hills Gardens     0.000000           0.000000           0.000000   
29         Fresh Meadows     0.000000           0.000000           0.000000   
30             Glen Oaks     0.000000           0.000000           0.000000   
31              Glendale     0.000000           0.000000           0.000000   
32               Hammels     0.000000           0.000000           0.000000   
33             Hillcrest     0.000000           0.000000           0.000000   
34                Hollis     0.000000           0.000000           0.000000   
35            Holliswood     0.000000           0.000000           0.000000   
36          Howard Beach     0.000000           0.000000           0.000000   
37         Hunters Point     0.014925           0.000000           0.000000   
38       Jackson Heights     0.000000           0.000000           0.000000   
39        Jamaica Center     0.000000           0.000000           0.000000   
40       Jamaica Estates     0.000000           0.000000           0.000000   
41         Jamaica Hills     0.000000           0.000000           0.000000   
42           Kew Gardens     0.000000           0.000000           0.000000   
43     Kew Gardens Hills     0.000000           0.000000           0.000000   
44             Laurelton     0.000000           0.000000           0.000000   
45           Lefrak City     0.000000           0.000000           0.000000   
46            Lindenwood     0.000000           0.000000           0.000000   
47           Little Neck     0.000000           0.000000           0.000000   
48      Long Island City     0.000000           0.000000           0.000000   
49                 Malba     0.000000           0.000000      

In [52]:
queens_grouped.describe()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
count    82.000000          82.000000          82.000000         82.000000   
mean      0.003710           0.001268           0.001301          0.000678   
std       0.014646           0.008969           0.008539          0.006135   
min       0.000000           0.000000           0.000000          0.000000   
25%       0.000000           0.000000           0.000000          0.000000   
50%       0.000000           0.000000           0.000000          0.000000   
75%       0.000000           0.000000           0.000000          0.000000   
max       0.083333           0.076923           0.066667          0.055556   

       American Restaurant  Antique Shop  Arepa Restaurant  \
count            82.000000     82.000000         82.000000   
mean              0.006124      0.003049          0.001154   
std               0.016266      0.027608          0.006499   
min               0.000000      0.000000          0.000000   
25%               0.000000      0.000000          0.000000   
50%               0.000000      0.000000          0.000000   
75%               0.000000      0.000000          0.000000   
max               0.090909      0.250000          0.043478   

       Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
count               82.000000    82.000000   82.000000            82.000000   
mean                 0.000553     0.000172    0.000172             0.004157   
std                  0.003899     0.001555    0.001555             0.029260   
min                  0.000000     0.000000    0.000000             0.000000   
25%                  0.000000     0.000000    0.000000             0.000000   
50%                  0.000000     0.000000    0.000000             0.000000   
75%                  0.000000     0.000000    0.000000             0.000000   
max                  0.033333     0.014085    0.014085             0.250000   

       Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
count             82.000000         82.000000           82.000000   
mean               0.000172          0.006119            0.001921   
std                0.001555          0.016042            0.009478   
min                0.000000          0.000000            0.000000   
25%                0.000000          0.000000            0.000000   
50%                0.000000          0.000000            0.000000   
75%                0.000000          0.000000            0.000000   
max                0.014085          0.076923            0.066667   

       Automotive Shop  BBQ Joint  Bagel Shop     Bakery       Bank  \
count        82.000000  82.000000   82.000000  82.000000  82.000000   
mean          0.001239   0.002061    0.008343   0.024013   0.021358   
std           0.007818   0.007577    0.016694   0.035566   0.033690   
min           0.000000   0.000000    0.000000   0.000000   0.000000   
25%           0.000000   0.000000    0.000000   0.000000   0.000000   
50%           0.000000   0.000000    0.000000   0.000000   0.000000   
75%           0.000000   0.000000    0.000000   0.048049   0.039583   
max           0.066667   0.043478    0.058824   0.130435   0.133333   

             Bar  Baseball Field  Basketball Court  Bath House      Beach  \
count  82.000000       82.000000         82.000000   82.000000  82.000000   
mean    0.012548        0.004422          0.003368    0.000254   0.027776   
std     0.025235        0.023604          0.018714    0.002301   0.122087   
min     0.000000        0.000000          0.000000    0.000000   0.000000   
25%     0.000000        0.000000          0.000000    0.000000   0.000000   
50%     0.000000        0.000000          0.000000    0.000000   0.000000   
75%     0.017435        0.000000          0.000000    0.000000   0.000000   
max     0.133333        0.142857          0.142857    0.020833   1.000000   

       Beach Bar  Bed & Breakfast  Beer Garden  Bike Trail     Bistro  \
coun

In [53]:
queens_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0          Arverne          0.0           0.000000                0.0   
1          Astoria          0.0           0.000000                0.0   
2  Astoria Heights          0.0           0.000000                0.0   
3       Auburndale          0.0           0.000000                0.0   
4      Bay Terrace          0.0           0.027027                0.0   

   Airport Terminal  American Restaurant  Antique Shop  Arepa Restaurant  \
0               0.0             0.000000           0.0               0.0   
1               0.0             0.010000           0.0               0.0   
2               0.0             0.000000           0.0               0.0   
3               0.0             0.050000           0.0               0.0   
4               0.0             0.054054           0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                   0.0               0.0                0.00   
1                   0.0               0.0                0.00   
2                   0.0               0.0                0.00   
3                   0.0               0.0                0.05   
4                   0.0               0.0                0.00   

   Automotive Shop  BBQ Joint  Bagel Shop    Bakery      Bank   Bar  \
0              0.0       0.00        0.00  0.000000  0.000000  0.00   
1              0.0       0.01        0.02  0.020000  0.000000  0.07   
2              0.0       0.00        0.00  0.076923  0.000000  0.00   
3              0.0       0.00        0.00  0.000000  0.000000  0.05   
4              0.0       0.00        0.00  0.027027  0.027027  0.00   

   Baseball Field  Basketball Court  Bath House     Beach  Beach Bar  \
0             0.0               0.0         0.0  0.055556        0.0   
1             0.0               0.0         0.0  0.000000        0.0   
2             0.0               0.0         0.0  0.000000        0.0   
3             0.0               0.0         0.0  0.000000        0.0   
4             0.0               0.0         0.0  0.000000        0.0   

   Bed & Breakfast  Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  \
0         0.055556         0.00         0.0     0.0    0.055556        0.0   
1         0.000000         0.01         0.0     0.0    0.000000        0.0   
2         0.000000         0.00         0.0     0.0    0.000000        0.0   
3         0.000000         0.00         0.0     0.0    0.000000        0.0   
4         0.000000         0.00         0.0     0.0    0.000000        0.0   

   Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  \
0       0.0       0.000000                  0.00             0.0      0.0   
1       0.0       0.000000                  0.01             0.0      0.0   
2       0.0       0.076923                  0.00             0.0      0.0   
3       0.0       0.000000                  0.00             0.0      0.0   
4       0.0       0.000000                  0.00             0.0      0.0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0             0.00     0.0       0.0      0.000000            0.0       0.0   
1             0.02     0.0       0.0      0.010000            0.0       0.0   
2             0.00     0.0       0.0      0.076923            0.0       0.0   
3             0.00     0.0       0.0      0.000000            0.0       0.0   
4             0.00     0.0       0.0      0.000000            0.0       0.0   

 

#### Let's confirm the new size

In [54]:
queens_grouped.shape

(82, 269)

#### Let's print each neighborhood along with the top 5 most common venues

In [55]:
num_top_venues = 5

for hood in queens_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = queens_grouped[queens_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
            venue  freq
0       Surf Spot  0.22
1   Metro Station  0.11
2  Sandwich Place  0.11
3           Beach  0.06
4      Board Shop  0.06


----Astoria----
                       venue  freq
0                        Bar  0.07
1  Middle Eastern Restaurant  0.06
2           Greek Restaurant  0.05
3                 Hookah Bar  0.05
4   Mediterranean Restaurant  0.04


----Astoria Heights----
                venue  freq
0       Deli / Bodega  0.08
1  Italian Restaurant  0.08
2         Bus Station  0.08
3       Bowling Alley  0.08
4         Supermarket  0.08


----Auburndale----
                venue  freq
0  Italian Restaurant  0.10
1       Deli / Bodega  0.05
2   Korean Restaurant  0.05
3   Mobile Phone Shop  0.05
4  Miscellaneous Shop  0.05


----Bay Terrace----
                 venue  freq
0       Clothing Store  0.11
1        Women's Store  0.05
2  American Restaurant  0.05
3           Donut Shop  0.05
4           Shoe Store  0.05


----Bayside----
               

               venue  freq
0  Korean Restaurant  0.48
1        Coffee Shop  0.04
2        Supermarket  0.04
3                Bar  0.04
4               Bank  0.04


----Neponsit----
          venue  freq
0         Beach   1.0
1   Yoga Studio   0.0
2    Nail Salon   0.0
3  Optical Shop   0.0
4        Office   0.0


----North Corona----
                  venue  freq
0         Deli / Bodega  0.17
1                Bakery  0.13
2           Pizza Place  0.09
3    Mexican Restaurant  0.09
4  Gym / Fitness Center  0.09


----Oakland Gardens----
                venue  freq
0  Chinese Restaurant  0.16
1   Korean Restaurant  0.12
2         Yoga Studio  0.08
3          Donut Shop  0.08
4                Bank  0.08


----Ozone Park----
         venue  freq
0  Pizza Place  0.09
1     Pharmacy  0.09
2        Diner  0.06
3          Gym  0.06
4         Bank  0.06


----Pomonok----
                 venue  freq
0                  Bar  0.09
1     Halal Restaurant  0.09
2                 Park  0.09
3        

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [56]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [57]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = queens_grouped['Neighborhood']

for ind in np.arange(queens_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(queens_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0          Arverne             Surf Spot              Metro Station   
1          Astoria                   Bar  Middle Eastern Restaurant   
2  Astoria Heights                 Plaza         Italian Restaurant   
3       Auburndale    Italian Restaurant               Noodle House   
4      Bay Terrace        Clothing Store              Women's Store   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0        Sandwich Place           Pizza Place               Coffee Shop   
1            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
2            Playground         Deli / Bodega               Bus Station   
3    Miscellaneous Shop      Sushi Restaurant    Furniture / Home Store   
4            Kids Store            Donut Shop         Mobile Phone Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0             Wine Shop            Donut Shop                 Beach   
1    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
2         Shopping Mall          Burger Joint         Bowling Alley   
3                   Bar        Discount Store    Athletics & Sports   
4            Shoe Store        Lingerie Store        Cosmetics Shop   

  9th Most Common Venue 10th Most Common Venue  
0       Thai Restaurant        Bed & Breakfast  
1           Pizza Place                    Gym  
2           Supermarket             Laundromat  
3           Supermarket      Mobile Phone Shop  
4   American Restaurant       Video Game Store

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [58]:
# set number of clusters
kclusters = 5

queens_grouped_clustering = queens_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(queens_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 3, 0, 0, 1], dtype=int32)

In [59]:
neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0          Arverne             Surf Spot              Metro Station   
1          Astoria                   Bar  Middle Eastern Restaurant   
2  Astoria Heights                 Plaza         Italian Restaurant   
3       Auburndale    Italian Restaurant               Noodle House   
4      Bay Terrace        Clothing Store              Women's Store   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0        Sandwich Place           Pizza Place               Coffee Shop   
1            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
2            Playground         Deli / Bodega               Bus Station   
3    Miscellaneous Shop      Sushi Restaurant    Furniture / Home Store   
4            Kids Store            Donut Shop         Mobile Phone Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0             Wine Shop            Donut Shop                 Beach   
1    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
2         Shopping Mall          Burger Joint         Bowling Alley   
3                   Bar        Discount Store    Athletics & Sports   
4            Shoe Store        Lingerie Store        Cosmetics Shop   

  9th Most Common Venue 10th Most Common Venue  
0       Thai Restaurant        Bed & Breakfast  
1           Pizza Place                    Gym  
2           Supermarket             Laundromat  
3           Supermarket      Mobile Phone Shop  
4   American Restaurant       Video Game Store

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [60]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

queens_clustered = merged_neighborhoods


queens_clustered = queens_clustered.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

queens_clustered # check the last columns!


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                  Astoria              40.768509              -73.915654   
1                  Astoria              40.768509              -73.915654   
2                  Astoria              40.768509              -73.915654   
3                  Astoria              40.768509              -73.915654   
4                  Astoria              40.768509              -73.915654   
5                  Astoria              40.768509              -73.915654   
6                  Astoria              40.768509              -73.915654   
7                  Astoria              40.768509              -73.915654   
8                  Astoria              40.768509              -73.915654   
9                  Astoria              40.768509              -73.915654   
10                 Astoria              40.768509              -73.915654   
11                 Astoria              40.768509              -73.915654   
12                 Astoria              40.768509              -73.915654   
13                 Astoria              40.768509              -73.915654   
14                 Astoria              40.768509              -73.915654   
15                 Astoria              40.768509              -73.915654   
16                 Astoria              40.768509              -73.915654   
17                 Astoria              40.768509              -73.915654   
18                 Astoria              40.768509              -73.915654   
19                 Astoria              40.768509              -73.915654   
20                 Astoria              40.768509              -73.915654   
21                 Astoria              40.768509              -73.915654   
22                 Astoria              40.768509              -73.915654   
23                 Astoria              40.768509              -73.915654   
24                 Astoria              40.768509              -73.915654   
25                 Astoria              40.768509              -73.915654   
26                 Astoria              40.768509              -73.915654   
27                 Astoria              40.768509              -73.915654   
28                 Astoria              40.768509              -73.915654   
29                 Astoria              40.768509              -73.915654   
30                 Astoria              40.768509              -73.915654   
31                 Astoria              40.768509              -73.915654   
32                 Astoria              40.768509              -73.915654   
33                 Astoria              40.768509              -73.915654   
34                 Astoria              40.768509              -73.915654   
35                 Astoria              40.768509              -73.915654   
36                 Astoria              40.768509              -73.915654   
37                 Astoria              40.768509              -73.915654   
38                 Astoria              40.768509              -73.915654   
39                 Astoria              40.768509              -73.915654   
40                 Astoria              40.768509              -73.915654   
41                 Astoria              40.768509              -73.915654   
42                 Astoria              40.768509              -73.915654   
43                 Astoria              40.768509              -73.915654   
44                 Astoria              40.768509              -73.915654   
45                 Astoria              40.768509              -73.915654   
46                 Astoria              40.768509              -73.915654   
47                 Astoria              40.768509              -73.915654   
48                 Astoria              40.768509              -73.915654   
49                 Astoria              40.768509              -73.915654   
50                 Astoria              40.768509              -73.915654   
51        

In [61]:
queens_clustered.groupby(['Cluster Labels']).size()

Cluster Labels
0    2077
1      99
2       1
3       8
4       4
dtype: int64

In [62]:
queens_clustered[queens_clustered.Neighborhood == 'Brooklyn Heights']

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2089  Brooklyn Heights              40.695864              -73.993782   
2090  Brooklyn Heights              40.695864              -73.993782   
2091  Brooklyn Heights              40.695864              -73.993782   
2092  Brooklyn Heights              40.695864              -73.993782   
2093  Brooklyn Heights              40.695864              -73.993782   
2094  Brooklyn Heights              40.695864              -73.993782   
2095  Brooklyn Heights              40.695864              -73.993782   
2096  Brooklyn Heights              40.695864              -73.993782   
2097  Brooklyn Heights              40.695864              -73.993782   
2098  Brooklyn Heights              40.695864              -73.993782   
2099  Brooklyn Heights              40.695864              -73.993782   
2100  Brooklyn Heights              40.695864              -73.993782   
2101  Brooklyn Heights              40.695864              -73.993782   
2102  Brooklyn Heights              40.695864              -73.993782   
2103  Brooklyn Heights              40.695864              -73.993782   
2104  Brooklyn Heights              40.695864              -73.993782   
2105  Brooklyn Heights              40.695864              -73.993782   
2106  Brooklyn Heights              40.695864              -73.993782   
2107  Brooklyn Heights              40.695864              -73.993782   
2108  Brooklyn Heights              40.695864              -73.993782   
2109  Brooklyn Heights              40.695864              -73.993782   
2110  Brooklyn Heights              40.695864              -73.993782   
2111  Brooklyn Heights              40.695864              -73.993782   
2112  Brooklyn Heights              40.695864              -73.993782   
2113  Brooklyn Heights              40.695864              -73.993782   
2114  Brooklyn Heights              40.695864              -73.993782   
2115  Brooklyn Heights              40.695864              -73.993782   
2116  Brooklyn Heights              40.695864              -73.993782   
2117  Brooklyn Heights              40.695864              -73.993782   
2118  Brooklyn Heights              40.695864              -73.993782   
2119  Brooklyn Heights              40.695864              -73.993782   
2120  Brooklyn Heights              40.695864              -73.993782   
2121  Brooklyn Heights              40.695864              -73.993782   
2122  Brooklyn Heights              40.695864              -73.993782   
2123  Brooklyn Heights              40.695864              -73.993782   
2124  Brooklyn Heights              40.695864              -73.993782   
2125  Brooklyn Heights              40.695864              -73.993782   
2126  Brooklyn Heights              40.695864              -73.993782   
2127  Brooklyn Heights              40.695864              -73.993782   
2128  Brooklyn Heights              40.695864              -73.993782   
2129  Brooklyn Heights              40.695864              -73.993782   
2130  Brooklyn Heights              40.695864              -73.993782   
2131  Brooklyn Heights              40.695864              -73.993782   
2132  Brooklyn Heights              40.695864              -73.993782   
2133  Brooklyn Heights              40.695864              -73.993782   
2134  Brooklyn Heights              40.695864              -73.993782   
2135  Brooklyn Heights              40.695864              -73.993782   
2136  Brooklyn Heights              40.695864              -73.993782   
2137  Brooklyn Heights              40.695864              -73.993782   
2138  Brooklyn Heights              40.695864              -73.993782   
2139  Brooklyn Heights              40.695864              -73.993782   
2140  Brooklyn Heights              40.695864              -73.993782   
2141  Brooklyn Heights              40.695864              -73.993782   
2142  Brooklyn Heights              40.695864              -73.99378

Finally, let's visualize the resulting clusters

In [63]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(queens_clustered['Neighborhood Latitude'], queens_clustered['Neighborhood Longitude'], queens_clustered['Neighborhood'], queens_clustered['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    
# add the initial place markers to map
for lat, lng, name in zip(brooklyn_my_place['Latitude'], brooklyn_my_place['Longitude'], brooklyn_my_place['Neighborhood']):
    folium.Marker(
        [lat, lng],
        icon= folium.Icon(color='red'), 
        popup=name).add_to(map_clusters)
       
map_clusters

In [64]:
queens_clustered.columns[[1]]

Index(['Neighborhood Latitude'], dtype='object')

In [65]:
queens_clustered.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                Venue  Venue Latitude  Venue Longitude        Venue Category  \
0        Favela Grill       40.767348       -73.917897  Brazilian Restaurant   
1      Orange Blossom       40.769856       -73.917012          Gourmet Shop   
2    Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop   
3     CrossFit Queens       40.769404       -73.918977                   Gym   
4  Simply Fit Astoria       40.769114       -73.912403                   Gym   

  Borough  Cluster Labels 1st Most Common Venue      2nd Most Common Venue  \
0  Queens               0                   Bar  Middle Eastern Restaurant   
1  Queens               0                   Bar  Middle Eastern Restaurant   
2  Queens               0                   Bar  Middle Eastern Restaurant   
3  Queens               0                   Bar  Middle Eastern Restaurant   
4  Queens               0                   Bar  Middle Eastern Restaurant   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
1            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
2            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
3            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   
4            Hookah Bar      Greek Restaurant  Mediterranean Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
1    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
2    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
3    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   
4    Seafood Restaurant     Indian Restaurant        Ice Cream Shop   

  9th Most Common Venue 10th Most Common Venue  
0           Pizza Place                    Gym  
1           Pizza Place                    Gym  
2           Pizza Place                    Gym  
3           Pizza Place                    Gym  
4           Pizza Place                    Gym

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [66]:
cluster_0=queens_clustered.loc[queens_clustered['Cluster Labels'] == 0]
cluster_0.loc[cluster_0['Borough'] == 'Brooklyn']
brooklyn_venues_final=cluster_0.loc[cluster_0['Borough'] == 'Brooklyn']
queens_venues_match=cluster_0.loc[cluster_0['Borough'] == 'Queens']
if(brooklyn_venues_final.shape[0]>0):
    if(queens_venues_match.shape[0]>0):
        print (queens_venues_match.Neighborhood.unique())

['Astoria' 'Woodside' 'Jackson Heights' 'Elmhurst' 'Howard Beach' 'Corona'
 'Forest Hills' 'Kew Gardens' 'Richmond Hill' 'Flushing'
 'Long Island City' 'Sunnyside' 'East Elmhurst' 'Maspeth' 'Ridgewood'
 'Glendale' 'Rego Park' 'Woodhaven' 'Ozone Park' 'South Ozone Park'
 'College Point' 'Whitestone' 'Bayside' 'Auburndale' 'Little Neck'
 'Douglaston' 'Glen Oaks' 'Bellerose' 'Kew Gardens Hills' 'Fresh Meadows'
 'Briarwood' 'Jamaica Center' 'Oakland Gardens' 'Queens Village' 'Hollis'
 'South Jamaica' 'St. Albans' 'Rochdale' 'Springfield Gardens'
 'Cambria Heights' 'Rosedale' 'Far Rockaway' 'Broad Channel' 'Steinway'
 'Beechhurst' 'Bay Terrace' 'Edgemere' 'Arverne' 'Murray Hill'
 'Floral Park' 'Holliswood' 'Jamaica Estates' 'Queensboro Hill'
 'Hillcrest' 'Ravenswood' 'Lindenwood' 'Lefrak City' 'Rockaway Park'
 'Bellaire' 'North Corona' 'Forest Hills Gardens' 'Jamaica Hills' 'Utopia'
 'Pomonok' 'Astoria Heights' 'Hunters Point' 'Sunnyside Gardens'
 'Blissville' 'Middle Village' 'Malba' 'Quee

#### Cluster 2

In [67]:
cluster_1=queens_clustered.loc[queens_clustered['Cluster Labels'] == 1]
brooklyn_venues_final=cluster_1.loc[cluster_1['Borough'] == 'Brooklyn']
queens_venues_match=cluster_1.loc[cluster_1['Borough'] == 'Queens']
if(brooklyn_venues_final.shape[0]>0):
    if(queens_venues_match.shape[0]>0):
        print (queens_venues_match.Neighborhood.unique())
        

#### Cluster 3

In [68]:
cluster_2=queens_clustered.loc[queens_clustered['Cluster Labels'] == 2]
brooklyn_venues_final=cluster_2.loc[cluster_2['Borough'] == 'Brooklyn']
queens_venues_match=cluster_2.loc[cluster_2['Borough'] == 'Queens']
if(brooklyn_venues_final.shape[0]>0):
    if(queens_venues_match.shape[0]>0):
        print (queens_venues_match.Neighborhood.unique())

#### Cluster 4

In [69]:
cluster_3=queens_clustered.loc[queens_clustered['Cluster Labels'] == 3]
brooklyn_venues_final=cluster_3.loc[cluster_3['Borough'] == 'Brooklyn']
queens_venues_match=cluster_3.loc[cluster_3['Borough'] == 'Queens']
if(brooklyn_venues_final.shape[0]>0):
    if(queens_venues_match.shape[0]>0):
        print (queens_venues_match.Neighborhood.unique())

#### Cluster 5

In [70]:
cluster_4=queens_clustered.loc[queens_clustered['Cluster Labels'] == 4]
brooklyn_venues_final=cluster_4.loc[cluster_4['Borough'] == 'Brooklyn']
queens_venues_match=cluster_4.loc[cluster_4['Borough'] == 'Queens']
if(brooklyn_venues_final.shape[0]>0):
    if(queens_venues_match.shape[0]>0):
        print (queens_venues_match.Neighborhood.unique())

# # Conclusion 

It is observed that the venues of Brooklyn Height largely fall under the cluster 0. Hence, Person X can move to any of the Cluster 0,  Queens Neighborhoods which are similar to Brooklyn Heights